#                                                        Machine Translation
##### "A Seq2Seq model employing an encoder-decoder architecture with LSTM units for translating sequences between languages."
This Seq2Seq model with an encoder-decoder architecture utilizes LSTM (Long Short-Term Memory) units to facilitate the translation of sequences between different languages.
The encoder phase processes input sequences, extracting their contextual information into a fixed-dimensional representation. This encoded information, often referred to as a "thought vector," is then passed to the decoder. 
The decoder utilizes this vector to generate output sequences, aiming to provide accurate translations.
LSTMs within both encoder and decoder components aid in capturing intricate sequential patterns, allowing the model to comprehend and translate complex linguistic structures, thereby enabling effective language translation.







### Importing Dependencies

In [12]:
import numpy as np
import pandas as pd
import os
import string
import re
from string import digits
from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.layers import Input, LSTM, Embedding, Dense
from tensorflow.keras.models import Model

### Reading Data

In [13]:
lines = pd.read_csv("Hindi_English_Truncated_Corpus.csv", encoding='utf-8')
lines.head()

source                                   english_sentence  \
0        ted  politicians do not have permission to do what ...   
1        ted         I'd like to tell you about one such child,   
2  indic2012  This percentage is even greater than the perce...   
3        ted  what we really mean is that they're bad at not...   
4  indic2012  .The ending portion of these Vedas is called U...   

                                      hindi_sentence  
0  राजनीतिज्ञों के पास जो कार्य करना चाहिए, वह कर...  
1  मई आपको ऐसे ही एक बच्चे के बारे में बताना चाहू...  
2   यह प्रतिशत भारत में हिन्दुओं प्रतिशत से अधिक है।  
3     हम ये नहीं कहना चाहते कि वो ध्यान नहीं दे पाते  
4        इन्हीं वेदों का अंतिम भाग उपनिषद कहलाता है।

### Data Preprocessing

In [14]:
# Analyzing Data from the 'source' Column
lines['source'].value_counts()
# Filtering Rows by 'source'
lines = lines[lines['source'] == 'ted']
# Displaying the Top Rows
print(lines.head(20))

   source                                   english_sentence  \
0     ted  politicians do not have permission to do what ...   
1     ted         I'd like to tell you about one such child,   
3     ted  what we really mean is that they're bad at not...   
7     ted   And who are we to say, even, that they are wrong   
13    ted                   So there is some sort of justice   
23    ted                                This changed slowly   
26    ted                               were being produced.   
30    ted        And you can see, this LED is going to glow.   
32    ted  to turn on the lights or to bring him a glass ...   
35    ted                       Can you imagine saying that?   
37    ted  Three: this is a good road in - right near whe...   
39    ted                                  What's going on?”   
42    ted   There are also financial reforms in rural China.   
49    ted  the family planning started in Vietnam and the...   
51    ted                    I mean, at 

In [15]:
# Removing Duplicates
lines.drop_duplicates(inplace=True)
print("Check isnull:-\n",pd.isnull(lines).sum())

# Contain only rows where 'english_sentence'column has non-null values.
lines = lines[~pd.isnull(lines['english_sentence'])]
lines = lines.sample(n=25000, random_state=42)
print(lines.shape)

Check isnull:-
 source              0
english_sentence    0
hindi_sentence      0
dtype: int64
(25000, 3)


In [16]:
# Lowercase all characters
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: x.lower())
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: x.lower())

# Remove quotes
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: re.sub("'", '', x))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: re.sub("'", '', x))

exclude = set(string.punctuation)  # Set of all special characters
# Remove all the special characters
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: ''.join(ch for ch in x if ch not in exclude))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: ''.join(ch for ch in x if ch not in exclude))

# Remove all numbers from text
remove_digits = str.maketrans('', '', digits)
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: x.translate(remove_digits))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: x.translate(remove_digits))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: re.sub("[२३०८१५७९४६]", "", x))

# Remove extra spaces
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: x.strip())
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: x.strip())
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: re.sub(" +", " ", x))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: re.sub(" +", " ", x))

# Add start and end tokens to target sequences
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: 'START_ ' + x + ' _END')
print(lines.head())

# Get English and Hindi Vocabulary
# Computes total number of unique words present in each language.
all_eng_words = set()
for eng in lines['english_sentence']:
    for word in eng.split():
        if word not in all_eng_words:
            all_eng_words.add(word)

all_hindi_words = set()
for hin in lines['hindi_sentence']:
    for word in hin.split():
        if word not in all_hindi_words:
            all_hindi_words.add(word)

print("all_eng_words: ", len(all_eng_words))
print("all_hindi_words: ", len(all_hindi_words))

       source                                   english_sentence  \
82040     ted  we still dont know who her parents are who she is   
85038     ted                                        no keyboard   
58018     ted                    but as far as being a performer   
74470     ted                        and this particular balloon   
122330    ted  and its not as hard as you think integrate cli...   

                                           hindi_sentence  
82040   START_ हम अभी तक नहीं जानते हैं कि उसके मातापि...  
85038                       START_ कोई कुंजीपटल नहीं _END  
58018             START_ लेकिन एक कलाकार होने के साथ _END  
74470                      START_ और यह खास गुब्बारा _END  
122330  START_ और जितना आपको लगता है यह उतना कठिन नहीं...  
all_eng_words:  14030
all_hindi_words:  17540


In [17]:
lines['length_eng_sentence'] = lines['english_sentence'].apply(lambda x: len(x.split(" ")))
lines['length_hin_sentence'] = lines['hindi_sentence'].apply(lambda x: len(x.split(" ")))
print(lines.head())

       source                                   english_sentence  \
82040     ted  we still dont know who her parents are who she is   
85038     ted                                        no keyboard   
58018     ted                    but as far as being a performer   
74470     ted                        and this particular balloon   
122330    ted  and its not as hard as you think integrate cli...   

                                           hindi_sentence  \
82040   START_ हम अभी तक नहीं जानते हैं कि उसके मातापि...   
85038                       START_ कोई कुंजीपटल नहीं _END   
58018             START_ लेकिन एक कलाकार होने के साथ _END   
74470                      START_ और यह खास गुब्बारा _END   
122330  START_ और जितना आपको लगता है यह उतना कठिन नहीं...   

        length_eng_sentence  length_hin_sentence  
82040                    11                   16  
85038                     2                    5  
58018                     7                    8  
74470               

In [18]:
# Perform filtering to ensure both English/Hindi sentences have lengths within specified range (20 words or fewer in this case)
# removing sentences that exceed this length limit.
# This helps in controlling length of sentences for further processing or modeling purposes.
lines = lines[lines['length_eng_sentence'] <= 20]
lines = lines[lines['length_hin_sentence'] <= 20]

print(lines.shape)
print("maximum length of Hindi Sentence ", max(lines['length_hin_sentence']))
print("maximum length of English Sentence ", max(lines['length_eng_sentence']))

(24774, 5)
maximum length of Hindi Sentence  20
maximum length of English Sentence  20


In [19]:
# Calculating the maximum lengths found in both sentences
max_length_src = max(lines['length_hin_sentence'])
max_length_tar = max(lines['length_eng_sentence'])

input_words = sorted(list(all_eng_words))
target_words = sorted(list(all_hindi_words))
num_encoder_tokens = len(all_eng_words)
num_decoder_tokens = len(all_hindi_words)
num_encoder_tokens, num_decoder_tokens

num_decoder_tokens += 1  # for zero padding

input_token_index = dict([(word, i + 1) for i, word in enumerate(input_words)])
target_token_index = dict([(word, i + 1) for i, word in enumerate(target_words)])

reverse_input_char_index = dict((i, word) for word, i in input_token_index.items())
reverse_target_char_index = dict((i, word) for word, i in target_token_index.items())

lines = shuffle(lines)
print(lines.head(10))

       source                                   english_sentence  \
4869      ted  went on until a new rabbi came rabbis always s...   
111293    ted                          we need help we need help   
13949     ted                okay induced pluripotent stem cells   
99133     ted                     and youre reading this website   
39270     ted  it could have been an english tudor or spanish...   
82906     ted                                    how do we allow   
31447     ted    while it is true that those things are going on   
42230     ted  they just get the school which parents choose ...   
82571     ted                   the family members the neighbors   
46515     ted                      this system costs you dollars   

                                           hindi_sentence  \
4869    START_ ये सब नए रब्बी के आने तक चला रब्बी हमेश...   
111293      START_ हमें मदद चाहिये। हमें मदद चाहिये। _END   
13949    START_ ठीक है प्रेरित pluripotent स्टेम सेल _END   
99133  

### Data Trainning/Evaluation

In [20]:
# Split the data into training and testing sets for both English/Hindi sentences.
X, y = lines['english_sentence'], lines['hindi_sentence']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

print(X_train.shape)
print(X_test.shape)
print(y_train.shape)
print(y_test.shape)

(19819,)
(4955,)
(19819,)
(4955,)


In [21]:
# Saving training/testing data into pickle files.
# uses to serialize object to a pickle format, allowing for easy storage and retrieval of data.
X_train.to_pickle('X_train.pkl')
X_test.to_pickle('X_test.pkl')

In [22]:
# Adjust sizes of encoder/decoder vocabularies by incrementing counts by 1 for zero padding.
num_encoder_tokens = len(input_token_index) + 1
num_decoder_tokens = len(target_token_index) + 1

# Check  whether index for padding(typically represented as 0)exists in encoder vocabulary
# If the padding index is missing, it's added to the vocabulary.
if 0 not in input_token_index.values():
    max_index = max(input_token_index.values())
    input_token_index['<PAD>'] = max_index + 1
    num_encoder_tokens += 1

# Define generate_batch function
# Each batch contains encoder input data, decoder input data, and decoder target data.
# This generator function is designed to continuously provide batches of preprocessed data 
# for training a sequence-to-sequence model, facilitating processing and learning of sequence data in ML model.
def generate_batch(X=X_train, y=y_train, batch_size=128):
    while True:
        for j in range(0, len(X), batch_size):
            encoder_input_data = np.zeros((batch_size, max_length_src), dtype='float32')
            decoder_input_data = np.zeros((batch_size, max_length_tar), dtype='float32')
            decoder_target_data = np.zeros((batch_size, max_length_tar, num_decoder_tokens), dtype='float32')
            for i, (input_text, target_text) in enumerate(zip(X[j:j + batch_size], y[j:j + batch_size])):
                for t, word in enumerate(input_text.split()):
                    encoder_input_data[i, t] = input_token_index.get(word, input_token_index['<PAD>'])

                for t, word in enumerate(target_text.split()):
                    if t < len(target_text.split()) - 1:
                        decoder_input_data[i, t] = target_token_index.get(word, 0)
                    if t > 0:
                        decoder_target_data[i, t - 1, target_token_index.get(word, 0)] = 1.
            yield ([encoder_input_data, decoder_input_data], decoder_target_data)

# 'latent_dim'represents Dimensionality of latent space or hidden state of model in NN architectures
latent_dim = 300
# Encoder architecture is being defined
encoder_inputs = Input(shape=(None,))
enc_emb = Embedding(num_encoder_tokens, latent_dim, mask_zero=True)(encoder_inputs)
encoder_lstm = LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder_lstm(enc_emb)
encoder_states = [state_h, state_c]
# Decoder architecture for a sequence-to-sequence model
decoder_inputs = Input(shape=(None,))
dec_emb_layer = Embedding(num_decoder_tokens, latent_dim, mask_zero=True)
dec_emb = dec_emb_layer(decoder_inputs)
decoder_lstm = LSTM(latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(dec_emb, initial_state=encoder_states)
decoder_dense = Dense(num_decoder_tokens, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

# Defines and compiles sequence-to-sequence model architecture using Keras.
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

model.summary()

# Trainning the defined model
train_samples = len(X_train)
val_samples = len(X_test)
batch_size = 128
epochs = 100
model.fit(x=generate_batch(X_train, y_train, batch_size=batch_size),
          steps_per_epoch=train_samples // batch_size,
          epochs=epochs,
          validation_data=generate_batch(X_test, y_test, batch_size=batch_size),
          validation_steps=val_samples // batch_size)

Model: "model_1"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_3 (InputLayer)        [(None, None)]               0         []                            
                                                                                                  
 input_4 (InputLayer)        [(None, None)]               0         []                            
                                                                                                  
 embedding_2 (Embedding)     (None, None, 300)            4209600   ['input_3[0][0]']             
                                                                                                  
 embedding_3 (Embedding)     (None, None, 300)            5262300   ['input_4[0][0]']             
                                                                                            

In [23]:
# Saving the trained model 
model.save_weights('nmt_weights.h5')

In [24]:
# Encode the input sequence to get the "thought vectors"
encoder_model = Model(encoder_inputs, encoder_states)

# Setsup placeholders for decoder's hidden state and cell state from previous time step. 
# Each of these placeholders is defined as a Keras Input layer Decoder setup
# Below tensors will hold the states of the previous time step
decoder_state_input_h = Input(shape=(latent_dim,))
decoder_state_input_c = Input(shape=(latent_dim,))
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]

# An Embedding layer for decoder-to obtain embeddings for decoder input sequences.
dec_emb2 = dec_emb_layer(decoder_inputs)
# To predict next word in the sequence, set initial states to states from previous time step
decoder_outputs2, state_h2, state_c2 = decoder_lstm(dec_emb2, initial_state=decoder_states_inputs)
decoder_states2 = [state_h2, state_c2]
decoder_outputs2 = decoder_dense(decoder_outputs2)

# Final decoder model
decoder_model = Model(
    [decoder_inputs] + decoder_states_inputs,
    [decoder_outputs2] + decoder_states2)

# Decodes input sequences using trained encoder/decoder models to generate predicted output sequences.
def decode_sequence(input_seq):
    states_value = encoder_model.predict(input_seq)
    target_seq = np.zeros((1, 1))
    target_seq[0, 0] = target_token_index['START_']

    stop_condition = False
    decoded_sentence = ''
    while not stop_condition:
        output_tokens, h, c = decoder_model.predict([target_seq] + states_value)

        sampled_token_index = np.argmax(output_tokens[0, -1, :])
        sampled_char = reverse_target_char_index[sampled_token_index]
        decoded_sentence += ' ' + sampled_char

        if (sampled_char == '_END' or len(decoded_sentence) > 50):
            stop_condition = True

        target_seq = np.zeros((1, 1))
        target_seq[0, 0] = sampled_token_index

        states_value = [h, c]

    return decoded_sentence

### Checking Predicted Output

In [25]:
train_gen = generate_batch(X_train, y_train, batch_size=1)
k = -1

k += 1
(input_seq, actual_output), _ = next(train_gen)
decoded_sentence = decode_sequence(input_seq)
print('Input English sentence:', X_train[k:k + 1].values[0])
print('Actual Hindi Translation:', y_train[k:k + 1].values[0][6:-4])
print('Predicted Hindi Translation:', decoded_sentence[:-4])

k+=1
(input_seq, actual_output), _ = next(train_gen)
decoded_sentence = decode_sequence(input_seq)
print('Input English sentence:', X_train[k:k+1].values[0])
print('Actual Hindi Translation:', y_train[k:k+1].values[0][6:-4])
print('Predicted Hindi Translation:', decoded_sentence[:-4])

k+=1
(input_seq, actual_output), _ = next(train_gen)
decoded_sentence = decode_sequence(input_seq)
print('Input English sentence:', X_train[k:k+1].values[0])
print('Actual Hindi Translation:', y_train[k:k+1].values[0][6:-4])
print('Predicted Hindi Translation:', decoded_sentence[:-4])

########################################################################################################################################################

1/1 [==============================] - 0s 24ms/step
Input English sentence: you get hints the actual steps for that problem
Actual Hindi Translation:  आपको सवाल पूर करने के लिये बीच के सारे कदम दिखाये जाते हैं 
Predicted Hindi Translation:  आपको सवाल पूर करने के लिये बीच के सारे कदम दिखाये 
1/1 [==============================] - 0s 20ms/step
Input English sentence: he said two interesting things
Actual Hindi Translation:  उन्होंने दो दिलचस्प बातें कही 
Predicted Hindi Translation:  उन्होंने दो दिलचस्प बातें कही 
1/1 [==============================] - 0s 20ms/step
Input English sentence: i didnt want to make it different from the men but it was different
Actual Hindi Translation:  मैं नहीं चाहती थी की यह पुरुषो से अलग हो लेकिन ये अलग था 
Predicted Hindi Translation:  मैं नहीं चाहती थी की यह पुरुषो से अलग हो लेकिन ये


### Analysing Crossentropy score and BLEU score

In [28]:
import nltk
from tensorflow.keras.preprocessing.sequence import pad_sequences

# Calculate cross-entropy score
test_gen = generate_batch(X_train, y_train, batch_size=1)
loss, accuracy = model.evaluate(test_gen, steps=len(X_train))

print(f"Cross-entropy Loss: {loss}")
print(f"Accuracy: {accuracy}")

19819/19819 [==============================] - 162s 8ms/step - loss: 0.0689 - accuracy: 0.9848
Cross-entropy Loss: 0.06885221600532532
Accuracy: 0.9848371148109436


In [27]:
from tqdm import tqdm
from nltk.translate.bleu_score import SmoothingFunction

def get_reference_and_candidate_sequences(X_test, y_test):
    predicted_sequences = []
    references = []

    for input_sentence, target_sentence in tqdm(zip(X_test, y_test), total=len(X_test)):
        input_sequence = []
        for word in input_sentence.split():
            if word in input_token_index:
                input_sequence.append(input_token_index[word])
            else:
                input_sequence.append(input_token_index['<PAD>'])

        input_sequence = pad_sequences([input_sequence], maxlen=max_length_src, padding='post')
        translated_seq = decode_sequence(input_sequence)
        translated_seq = translated_seq.split()
        predicted_sequences.append(translated_seq)

        references.append(target_sentence.split())

    return references, predicted_sequences

references, candidates = get_reference_and_candidate_sequences(X_test, y_test)

# Using SmoothingFunction to handle cases where there are zero n-gram overlaps
smoother = SmoothingFunction()
bleu_score = nltk.translate.bleu_score.corpus_bleu(references, candidates, smoothing_function=smoother.method1)
print(f"BLEU Score: {bleu_score}")


  0%|          | 0/4955 [00:00<?, ?it/s]

1/1 [==============================] - 0s 20ms/step


  0%|          | 1/4955 [00:01<1:49:41,  1.33s/it]

1/1 [==============================] - 0s 19ms/step


  0%|          | 2/4955 [00:01<58:10,  1.42it/s]  

...

1/1 [==============================] - 0s 20ms/step


100%|█████████▉| 4954/4955 [46:46<00:00,  1.69it/s]

1/1 [==============================] - 0s 19ms/step


100%|██████████| 4955/4955 [46:47<00:00,  1.76it/s]


BLEU Score: 1.487926620222595e-05
